## Local Inference on GPU
Model page: https://huggingface.co/SmilingWolf/wd-vit-tagger-v3

⚠️ If the generated code snippets do not work, please open an issue on either the [model repo](https://huggingface.co/SmilingWolf/wd-vit-tagger-v3)
			and/or on [huggingface.js](https://github.com/huggingface/huggingface.js/blob/main/packages/tasks/src/model-libraries-snippets.ts) 🙏

In [ ]:

%cd /content/
!unzip training_data.zip




In [ ]:
# @markdown Split the image into 20 parts prior to running
no_parts = 1 # @param {type:'slider', min:1,max:30,step:1}
print(f'Splitting all images found under /content/... \n into {no_parts} along x-axis')
import os,math,random
from PIL import Image
home_directory = '/content/'
using_Kaggle = os.environ.get('KAGGLE_URL_BASE','')
if using_Kaggle : home_directory = '/kaggle/working/'
%cd {home_directory}

def my_mkdirs(folder):
  if os.path.exists(folder)==False:
    os.makedirs(folder)


tgt_folder = f'/content/tmp/'
split_folder = f'/content/input_images/'
my_mkdirs(f'{split_folder}')


src_folder = '/content/'
suffixes = ['.gif','.png', '.jpeg' , '.webp' , '.jpg']
num = 1
for filename in os.listdir(src_folder):
  for suffix in suffixes:
    if not filename.find(suffix)>-1: continue
    #while os.path.exists(f'{tgt_folder}{num}.txt'):num = num+1
    print(filename)
    %cd {src_folder}
    textpath = filename.replace(suffix,'.txt')
    #os.remove(f'{filename}')
    #continue
    image = Image.open(f"{filename}").convert('RGB')
    w,h=image.size
    #grid = product(range(0, h-h%d, d), range(0, w-w%d, d))
    divs=no_parts
    step=math.floor(w/divs)
    %cd {split_folder}
    for index in range(divs):
        box = (step*index, 0 ,step*(index+1),math.floor(1.0*h))
        image.crop(box).save(f'{num}_{index}.jpeg','JPEG')
        %cd /content/
        if os.path.exists(textpath):
          with open(f'{textpath}', 'r') as file:
            _tags = file.read()

            print(_tags)
            if not _tags:continue
            tags=''
            _tags = [item.strip() for item in f'{_tags}'.split(',')]
            random.shuffle(_tags)
            for tag in _tags:
              tags = tags + tag + ' , '
            #----#
            tags = (tags + 'AAAA').replace(' , AAAA','')
            prompt_str = f' {tags}'
            %cd {split_folder}
            f = open(f'{num}_{index}.txt','w')
            f.write(f'{prompt_str}')
            f.close()
          #---#
        #-----#
    #----#
    num = num+1
    #caption = stream_chat(input_image, "descriptive", "formal", "any")
    #print(f"...\n\n...caption for {filename}\n\n...")
    #print(caption)
    #---------#
    #f = open(f"{num}.txt", "w")
    #f.write(f'{caption}')
    #f.close()
    #input_image.save(f'{num}.jpeg', "JPEG")
    os.remove(f"{src_folder}{filename}")
    #os.remove(f'{src_folder}{textpath}')

In [ ]:
# Install required packages
!pip install timm pillow pandas requests

import os
import timm
import torch
from PIL import Image
import torchvision.transforms as transforms
import numpy as np
import pandas as pd
import requests
from io import StringIO

# Download the selected_tags.csv file
tags_url = "https://huggingface.co/SmilingWolf/wd-vit-tagger-v3/resolve/main/selected_tags.csv"
response = requests.get(tags_url)
if response.status_code != 200:
    raise Exception(f"Failed to download selected_tags.csv: Status code {response.status_code}")
tags_df = pd.read_csv(StringIO(response.text))
tags = tags_df['name'].tolist()  # Extract tag names from the CSV
print(f"Loaded {len(tags)} tags from CSV: {tags[:10]}...")  # Print first 10 tags for verification

# Set up the model
model = timm.create_model("hf_hub:SmilingWolf/wd-vit-tagger-v3", pretrained=True)
model.eval()
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
model = model.to(device)
print(f"Model loaded on device: {device}")

# Verify model output size
dummy_input = torch.zeros(1, 3, 448, 448).to(device)
with torch.no_grad():
    dummy_output = model(dummy_input)
model_output_size = dummy_output.shape[1]
print(f"Model output size: {model_output_size}")

# Check if tags length matches model output
if len(tags) != model_output_size:
    raise ValueError(f"Tag list length ({len(tags)}) does not match model output size ({model_output_size})")

# Define image preprocessing
preprocess = transforms.Compose([
    transforms.Resize((448, 448)),
    transforms.ToTensor(),
    transforms.Normalize(mean=[0.485, 0.456, 0.406], std=[0.229, 0.224, 0.225]),
])

# Set paths
input_folder = "/content/input_images"  # Change to your input folder path
output_folder = "/content/tmp"  # Change to your output folder path

# Create output folder if it doesn't exist
os.makedirs(output_folder, exist_ok=True)

# Function to process an image and generate tags
def process_image(image_path, tags_list):
    try:
        # Load and preprocess image
        image = Image.open(image_path).convert("RGB")
        input_tensor = preprocess(image).unsqueeze(0).to(device)

        # Get model predictions
        with torch.no_grad():
            logits = model(input_tensor)

        # Apply sigmoid to get probabilities
        probs = torch.sigmoid(logits).cpu().numpy()[0]

        # Ensure probs length matches tags length
        if len(probs) != len(tags_list):
            raise ValueError(f"Model output ({len(probs)}) does not match tags length ({len(tags_list)}) for {image_path}")

        # Get tags with probability > 0.5 (adjust threshold as needed)
        selected_tags = [tags_list[i] for i, prob in enumerate(probs) if prob > 0.5]

        return selected_tags, image
    except Exception as e:
        raise Exception(f"Error in process_image for {image_path}: {str(e)}")

# Process all images in the input folder
for filename in sorted(os.listdir(input_folder)):  # Sort for reproducibility
    if filename.lower().endswith(('.png', '.jpg', '.jpeg', '.bmp', '.gif')):
        image_path = os.path.join(input_folder, filename)

        # Generate tags and get processed image
        try:
            selected_tags, image = process_image(image_path, tags)  # Pass tags explicitly

            # Define output paths
            base_name = os.path.splitext(filename)[0]
            output_image_path = os.path.join(output_folder, f"{base_name}.jpg")
            output_txt_path = os.path.join(output_folder, f"{base_name}.txt")

            # Save image as JPG
            image.save(output_image_path, "JPEG", quality=95)

            # Save tags to text file
            with open(output_txt_path, "w") as f:
                f.write(", ".join(selected_tags))

            print(f"Processed {filename}: {selected_tags}")
        except Exception as e:
            print(f"Error processing {filename}: {str(e)}")
            continue

print("Processing complete!")

In [ ]:
import shutil
%cd /content/
shutil.make_archive('/content/tmp', 'zip', '/content/tmp')